# Filtering for BVP, ACC data:
1. Chebyshev II filter on BVP data
2. Butterworth filter on accelerometer data
3. Accelerometer upsampling


In [149]:
import heartpy as hp
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
%matplotlib notebook
import plotly.express as px
from scipy import signal, interpolate

In [150]:
os.getcwd()
os.chdir("C:\\Users\\Owner\\Rutgers University\\Michelle Chen - Rutgers_Neuropsych_Lab\\COVID_Fatigue\\RC_award\\Data\\Concatenated_Data")

In [151]:
df = pd.read_csv('cov4_lab.csv') 
df_bvp = df['BVP (64 Hz)'].to_numpy()

## Part 1: Chebyshev Filtering of BVP data

In [152]:
# Define filter parameters
order = 4      # Order of the filter
stopband_attenuation = 40   # Minimum attenuation required in the stopband (in dB)

# when i experiment with stopband val, i dont see a noticable change from 2-25ish
cutoff_frequency = 4       # Cutoff frequency in Hz (adjust as needed)
sampling_rate = 64.0          # The sampling rate of your BVP signal

#favorite values so far: order 4, sa 40, cf 3

# Design the Chebyshev type II filter
sos = signal.cheby2(N=order, rs=stopband_attenuation, Wn=cutoff_frequency, btype='lowpass', fs=sampling_rate, output='sos')

# Apply the filter to your BVP signal
filtered_bvp = signal.sosfilt(sos, df_bvp)
df['BVP_filtered'] = filtered_bvp
new_cols = ["timestamp","BVP (64 Hz)","BVP_filtered","EDA (4 Hz)","TEMP (4 Hz)","ACC X (32 Hz)","ACC Y (32 Hz)","ACC Z (32 Hz)","Block","Fatigue_Rating"]
df = df[new_cols]

In [167]:
#Display filtered BVP data in an interactive graph
bl0 = df[df['Block']==0]
fig = px.line(bl0, x='timestamp', y=df.columns[1:3], title='Baseline Filtered BVP Signal')
fig.show()

## Part 2: Filtering the Accelerometer data. 

In [154]:
#first need to remove NaN values
df_acc = df.copy()
df_acc.dropna(subset="ACC X (32 Hz)", inplace=True)

In [155]:
#We will use a butterworth filter
acc_x = df_acc['ACC X (32 Hz)'].to_numpy() 
acc_y = df_acc['ACC Y (32 Hz)'].to_numpy() 
acc_z = df_acc['ACC Z (32 Hz)'].to_numpy() 

# changeable parameters
sampling_rate = 32 #don't change
order = 4 
cutoff_frequency = 4 

butter_sos = signal.butter(N=order, Wn=cutoff_frequency, btype='low', fs=sampling_rate, output='sos')

acc_x_filtered = signal.sosfilt(butter_sos, acc_x)
acc_y_filtered = signal.sosfilt(butter_sos, acc_y)
acc_z_filtered = signal.sosfilt(butter_sos, acc_z)

df_acc['ACC_X_filtered'] = acc_x_filtered
df_acc['ACC_Y_filtered'] = acc_y_filtered
df_acc['ACC_Z_filtered'] = acc_z_filtered
new_cols = ["timestamp","ACC X (32 Hz)","ACC_X_filtered","ACC Y (32 Hz)","ACC_Y_filtered","ACC Z (32 Hz)","ACC_Z_filtered","Block"]
df_acc_filt = df_acc[new_cols]

In [156]:
# plot original vs. filtered for each axis
bl1 = df_acc_filt[df_acc_filt['Block']==1]
fig = px.line(bl1, x='timestamp', y=df_acc_filt.columns[1:3], title='Block 1 Filtered ACC X Signal')
#fig.show()

In [157]:
# y axis
bl1 = df_acc_filt[df_acc_filt['Block']==1]
fig = px.line(bl1, x='timestamp', y=df_acc_filt.columns[3:5], title='Block 1 Filtered ACC Y Signal')
#fig.show()

In [158]:
# z axis
bl1 = df_acc_filt[df_acc_filt['Block']==1]
fig = px.line(bl1, x='timestamp', y=df_acc_filt.columns[5:7], title='Block 1 Filtered ACC Z Signal')
#fig.show()

In [159]:
# all 3, just for the fun of it
# plot original vs. filtered for each axis
bl1 = df_acc_filt[df_acc_filt['Block']==1]
fig = px.line(bl1, x='timestamp', y=df_acc_filt.columns[1:7], title='Block 1 Filtered ACC Signal')
#fig.show()

## Part 3: Upsampling the Accelerometer Data

In [160]:
# combine back into main dataframe
acc_filt = df_acc_filt.drop(df_acc_filt.columns[-1], axis=1)

mdf = pd.merge(df, acc_filt, on='timestamp', how="left")
reorder = ["timestamp","BVP (64 Hz)","BVP_filtered",
           "ACC_X_filtered","ACC_Y_filtered","ACC_Z_filtered",
           "EDA (4 Hz)","TEMP (4 Hz)","Block","Fatigue_Rating"]
mdf = mdf[reorder]

In [162]:
# LINEAR INTERPOLATION
mdf['timestamp'] = pd.to_datetime(mdf['timestamp'])

acc32 = ["ACC_X_filtered","ACC_Y_filtered","ACC_Z_filtered"]
acc_linear = ["ACC_X_linear", "ACC_Y_linear", "ACC_Z_linear"]
mdf[acc_linear] = mdf[acc32].interpolate(method='linear')

In [163]:
# POLYNOMIAL INTERPOLATION (order 3)
acc_poly = ["ACC_X_poly", "ACC_Y_poly", "ACC_Z_poly"]
mdf[acc_poly] = mdf[acc32].interpolate(method='polynomial', order=3)

# polynomial interpolation won't interpolate the last value if it is NaN. for now, just pad it
mdf[acc_poly] = mdf[acc_poly].interpolate(method='pad')

In [142]:
# SPLINE INTERPOLATION (cubic spline)
acc_spline = ["ACC_X_spline", "ACC_Y_spline", "ACC_Z_spline"]
mdf[acc_spline] = mdf[acc32].interpolate(method='spline', order=3)

In [164]:
# graph interpolated methods against each other (and maybe old data if you can figure it out)
bl = mdf[mdf['Block']==1]
fig = px.line(bl, x='timestamp', y=mdf.columns[10:20], title='Block 1 Filtered BVP & ACC')
#fig.show()

In [165]:
reorder = ["timestamp","BVP_filtered",
           "ACC_X_poly","ACC_Y_poly","ACC_Z_poly",
           "EDA (4 Hz)","TEMP (4 Hz)","Block","Fatigue_Rating"]
mdf = mdf[reorder]

In [166]:
# ALL THE DATA
bl = mdf[mdf['Block']==1]
fig = px.line(bl, x='timestamp', y=mdf.columns[1:5], title='Block 1 Filtered BVP & ACC')
#fig.show()

In [147]:
# Saving dataframes
nwd = 'C:\\Users\\Owner\\Rutgers University\\Michelle Chen - Rutgers_Neuropsych_Lab\\COVID_Fatigue\\RC_award\\Data\\Concatenated_Data\\'

mdf.to_csv(nwd + 'Cov4_lab_filtered.csv', index=False)
